In [1]:
import os
!git clone https://github.com/jnordberg/tortoise-tts.git
os.chdir('tortoise-tts')
!pip install -r requirements.txt
!pip install transformers==4.19.0 einops==0.5.0 rotary_embedding_torch==0.1.5 unidecode==1.3.5
!pip install setuptools
!pip install .

Cloning into 'tortoise-tts'...
remote: Enumerating objects: 1481, done.
remote: Total 1481 (delta 0), reused 0 (delta 0), pack-reused 1481 (from 1)
Receiving objects: 100% (1481/1481), 53.56 MiB | 40.78 MiB/s, done.
Resolving deltas: 100% (604/604), done.
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 38.5 MB/s eta 0:00:0000:01
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.8/110.8 kB 7.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of librosa to determine which version is compatible with other requirements. This could take a while.
INFO: pip is looking at multiple versions of resampy to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5

In [2]:
# Imports used through the rest of the notebook.
import torch
import torchaudio
import torch.nn as nn
import torch.nn.functional as F

import IPython

from tortoise.api import TextToSpeech
from tortoise.utils.audio import load_audio, load_voice, load_voices

# This will download all the models used by Tortoise from the HuggingFace hub.
tts = TextToSpeech()

Downloading:   0%|          | 0.00/2.06k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.18G [00:00<?, ?B/s]

/opt/conda/lib/python3.10/site-packages/transformers/modeling_utils.py:392: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  return torch.load(checkpoint_file, map_location="cp

Downloading:   0%|          | 0.00/159 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.57k [00:00<?, ?B/s]

...

100% |########################################################################|


Done.


100% |########################################################################|


Done.


/kaggle/working/tortoise-tts/tortoise/api.py:196: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  self.autoregressive.load_state_dict(torch.load(f'{models_dir}/autoregressive.

In [3]:
%%writefile speech.txt

'''Global efforts to combat climate change are gaining momentum as countries around the world pledge to reduce carbon emissions. The United Nations has called for urgent action to limit global warming to 1.5 degrees Celsius above pre-industrial levels, and governments are responding with ambitious plans.

In the technology sector, major advancements in artificial intelligence are continuing to shape the future of industries from healthcare to finance, AI is transforming how businesses operate, offering new opportunities for efficiency and innovation.

Meanwhile, in the world of sports, the upcoming Olympic Games are set to captivate audiences worldwide. Athletes are preparing to compete on the global stage, showcasing their skills and determination. The event promises to be a thrilling spectacle, with new records expected to be set.

Finally, in entertainment, a highly anticipated movie release is breaking box office records. The film, which features groundbreaking visual effects and a star-studded cast, has garnered rave reviews from critics and audiences alike.'''

Writing speech.txt


In [5]:
from tortoise.utils.text import split_and_recombine_text
from time import time
import os

outpath = "results/longform/"

textfile_path = "/kaggle/working/tortoise-tts/speech.txt"

CUSTOM_VOICE_NAME='lj'
# Process text
with open(textfile_path, 'r', encoding='utf-8') as f:
    text = ' '.join([l for l in f.readlines()])
    if '|' in text:
        print("Found the '|' character in your text, which I will use as a cue for where to split it up. If this was not"
              "your intent, please remove all '|' characters from the input.")
        texts = text.split('|')
    else:
        texts = split_and_recombine_text(text)

seed = int(time())

voice_outpath = os.path.join(outpath, CUSTOM_VOICE_NAME)
os.makedirs(voice_outpath, exist_ok=True)

voice_samples, conditioning_latents = load_voice(CUSTOM_VOICE_NAME)

all_parts = []
for j, text in enumerate(texts):
    gen = tts.tts_with_preset(text, voice_samples=voice_samples, conditioning_latents=conditioning_latents,
                              preset="standard", k=1, use_deterministic_seed=seed,length_penalty=1.0,cond_free_k=3)
    gen = gen.squeeze(0).cpu()
    torchaudio.save(os.path.join(voice_outpath, f'{j}.wav'), gen, 24000)
    all_parts.append(gen)

full_audio = torch.cat(all_parts, dim=-1)
torchaudio.save(os.path.join(voice_outpath, 'combined.wav'), full_audio, 24000)
IPython.display.Audio(os.path.join(voice_outpath, 'combined.wav'))

Generating autoregressive samples..


100%|██████████| 16/16 [01:18<00:00,  4.92s/it]


Computing best candidates using CLVP and CVVP


100%|██████████| 16/16 [00:21<00:00,  1.34s/it]


Transforming autoregressive outputs into audio..


...

100%|██████████| 16/16 [01:36<00:00,  6.00s/it]


Computing best candidates using CLVP and CVVP


100%|██████████| 16/16 [00:22<00:00,  1.39s/it]


Transforming autoregressive outputs into audio..


100%|██████████| 200/200 [00:57<00:00,  3.47it/s]


In [19]:
import librosa
import numpy as np
hop_length = 512
db_threshold = -45

def trim_audio(audio):
    generated_audio = audio.squeeze().numpy()
    audio_rms = librosa.feature.rms(y=generated_audio, frame_length=2048, hop_length=hop_length)[0]
    audio_db = librosa.power_to_db(audio_rms**2, ref=np.max)

    start_index, end_index = None, None
    for index, frame_rms in enumerate(audio_db):
        if frame_rms >= db_threshold:
            if start_index is None:
                    start_index = index
        elif start_index is not None:
            end_index = index - 1
            break

    return audio.squeeze(0)[:, start_index*hop_length:end_index*hop_length]

In [ ]:
text='''Global efforts to combat climate change are gaining momentum as countries worldwide pledge to reduce carbon emissions, responding to the United Nations urgent call to limit global warming to 1.5 degrees Celsius above pre-industrial levels. At the same time, major advancements in artificial intelligence are continuing to shape the future of industries, transforming sectors like healthcare and finance by offering new opportunities for efficiency and innovation. Meanwhile, the upcoming Olympic Games are set to captivate audiences globally, with athletes preparing to showcase their skills and determination on the world stage, promising a thrilling spectacle with potential new records. In entertainment, a highly anticipated movie release, featuring groundbreaking visual effects and a star-studded cast, is breaking box office records, earning rave reviews from critics and audiences alike.'''

In [ ]:
#https://github.com/smtiitm/Fastspeech2_HS/blob/main/inference.py hindi inference